**Goal:** Create a database, fill with historical tree data, and query data.

**Why:** Downtown Improvement District's project to track trees will benefit from using a relational database to store, collect, and report on the data available.

**Steps:**

First, open a program that can connect to a SQL database, such as Azure Data Studio or SQL Server Management Studio. If you're reading this notebook, chances are you already have the program open! Nice job.

Next, create the database by running the code below. 

_Note:_ When you see a grey box such as the box below that says "CREATE DATABASE Trees;", there is code to run. To activate this code, you can either click the "Run cell" button in the grey box below, or copy & paste the code into a new query window. The code is embedded here so that we can explain each step along the way.

In [5]:
CREATE DATABASE Trees;

Commands completed successfully.

Total execution time: 00:00:00.323

Then, create the tables in the database.

In [3]:
USE Trees
GO
CREATE TABLE [dbo].[TreeKeeper_Staging] (
    [Species]                              NVARCHAR (MAX) NULL,
    [DBH]                                  FLOAT (53)     NULL,
    [Condition for ISA value]              NVARCHAR (MAX) NULL,
    [Urban Forestry Maintenance]           NVARCHAR (MAX) NULL,
    [Location Type for ISA value]          NVARCHAR (MAX) NULL,
    [Planting Width MinAvailableRootSpace] NVARCHAR (MAX) NULL,
    [Service Area]                         NVARCHAR (MAX) NULL,
    [Neighborhood]                         NVARCHAR (MAX) NULL,
    [Park]                                 NVARCHAR (MAX) NULL,
    [Primary Wires Overhead]               NVARCHAR (MAX) NULL,
    [Lights or Conduit at Tree Site]       NVARCHAR (MAX) NULL,
    [Tree Watering Bag]                    NVARCHAR (MAX) NULL,
    [Tree Stake]                           NVARCHAR (MAX) NULL,
    [Tree Grate]                           NVARCHAR (MAX) NULL,
    [Structure Soil Type]                  NVARCHAR (MAX) NULL,
    [Treated Tree]                         NVARCHAR (MAX) NULL,
    [Research Tree]                        NVARCHAR (MAX) NULL,
    [Removal Cause]                        NVARCHAR (MAX) NULL,
    [Removal DBH]                          FLOAT (53)     NULL,
    [Size]                                 NVARCHAR (MAX) NULL,
    [Root]                                 NVARCHAR (MAX) NULL,
    [Planting Project]                     NVARCHAR (MAX) NULL,
    [Unique Planting Situation]            NVARCHAR (MAX) NULL,
    [Stump Grinding]                       NVARCHAR (MAX) NULL,
    [Contact Info]                         NVARCHAR (MAX) NULL,
    [Stump Size]                           NVARCHAR (MAX) NULL,
    [Preservation Project]                 NVARCHAR (MAX) NULL,
    [Preservation Type]                    NVARCHAR (MAX) NULL,
    [Root Damage]                          NVARCHAR (MAX) NULL,
    [Stem Damage]                          NVARCHAR (MAX) NULL,
    [Canopy Damage]                        NVARCHAR (MAX) NULL,
    [Damage Extent]                        NVARCHAR (MAX) NULL,
    [Underground Utility Conflict]         NVARCHAR (MAX) NULL,
    [Tree Inspector Area]                  NVARCHAR (MAX) NULL,
    [Maintenance Task]                     NVARCHAR (MAX) NULL,
    [Tree Planted Date]                    NVARCHAR (MAX) NULL,
    [Address]                              NVARCHAR (MAX) NULL,
    [On Street]                            NVARCHAR (MAX) NULL,
    [From Street]                          NVARCHAR (MAX) NULL,
    [To Street]                            NVARCHAR (MAX) NULL,
    [X-Coord]                              FLOAT (53)     NULL,
    [Y-Coord]                              FLOAT (53)     NULL,
    [Inventory Date]                       NVARCHAR (MAX) NULL,
    [Change Date]                          DATE           NULL,
    [Comment]                              NVARCHAR (MAX) NULL,
    [Site ID]                              INT            NOT NULL
);



Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.010

The above code creates three tables:

1. **TreeKeeper\_staging:** This table is for the staging of data from TreeKeeper's source data. The columns' datatypes are generally not restrictive (i.e. a date column like "Inventory Date" allows for non-date values) because the source data can be inconsistent! The goal here is to import the data in any form. We will worry about cleaning this data in a subsequent step. 
2. **tree:** This

**Export data from Excel to TSV** 

Next, extract the source data from Excel to a tab-separated values (TSV) text file. 

1. In the Excel data file, click **File \> Save As...**
2. In the **Save as type** dropdown box, select **Text (tab delimited) (\*.txt)** option.
3. Click **Save**.

Write down the filepath where you saved the file.

_Note:_ You cannot use CSV file format for this tree data, because the source data cells can contain commas. If you run into an issue using a tab-separated values file, you can export the data from Excel to a pipe-delimited file following [this tutorial](https://www.automateexcel.com/how-to/convert-save-as-pipe-delimited/).

Each cell will be delimited by a tab, and each row will be delimited by a Windows-standard line break ('CRLF'). 

Examine the file in Notepad++ or a similar text editor. Verify that the first row is the header row (i.e. that it contains the column titles, "Species DBH Condition for ISA value Urban Forestry Maintenance" etc) and that the rest of the file looks to be complete.

_Note:_ If the first row is not the header row, but instead starts immediately with the data, then do this: change the line "FIRSTROW = 2" below to "FIRSTROW = 1", or remove it.

**Import data into SQL Database**

Replace the filepath in the code below, 'C:\\temp\\example\_data.tsv', with the filepath where you saved the TSV file from the previous step.

In [1]:
BULK INSERT TreeKeeper_Staging
FROM 'C:\temp\example_data.tsv'
WITH (
	FIELDTERMINATOR = '\t',
	FIRSTROW = 2
)
GO

(31582 rows affected)

Total execution time: 00:00:01.702

If the data operation completed successfully, you should see a note (xx rows affected). If you see errors, examine the line referenced by the error message and fix.

**Examine data**

Run the code below to display the data you just imported.

In [ ]:
SELECT *
FROM TreeKeeper_Staging


**Step 2: Create more tables to handle the data**

We will create the remainder of the tables:

1. **KeyValue\_LocType**: This table contains key-value pairs for the Location Type ("Location Type for ISA Value" column). We will use this table to make sure the imported data's location types match the expected data types (by using a foreign key constraint in the next table.) This constraint helps catch typos and ensure clean data.
2. **Trees:** This table is the main data table from which we will analyze trees. The table stores only the necessary columns and we will clean/validate the rows of the staging table before writing them to **Trees** table. 
3. **TreeKeeper\_Errors**: This table stores the errors that were found during validation of staging data. These rows need to be fixed/cleaned before they can be stored in **Trees**.

   Run the code below to create these tables.

In [ ]:
USE Trees; -- this line ensures the program uses the database we've created

-- Create table for the location types, mapped with key-value pairs in alphabetical order
DROP TABLE IF EXISTS KeyValue_LocType;
CREATE TABLE KeyValue_LocType (
  ID int NOT NULL,
  Value nvarchar(255),
  PRIMARY KEY (ID)
)

-- Populate our known location types into the newly created table
INSERT INTO KeyValue_LocType ( ID, Value )
VALUES 
  (1, 'Easement Tree'),
  (2, 'OtherCityProperty (Pol-Fir-PW-P&Scem-etc'),
  (3, 'Parkland/Golf Course'),
  (4, 'Street Tree (Boulevard)'),
  (5, 'Street Tree (Median)'),
  (6, 'Woodland/Natural Area')

-- Create table for import source; this will be stored as metadata to track Trees row source
CREATE TABLE KeyValue_ImportSource (
  ID      SMALLINT NOT NULL,
  Value   NVARCHAR(255),
  PRIMARY KEY (ID)
)
-- Populate the table with import source values
INSERT INTO KeyValue_ImportSource
VALUES
    (1,'Flat File'),
    (2,'Error Table'),
    (3,'Manual Entry')

-- Create a table for tree data. We will move the imported data from TreeKeeper_Staging to the Trees table.
--      The Trees table will be lighter and cleaner, which will make for better performance and usability.  
CREATE TABLE [dbo].[Trees] (
    PK                        INT IDENTITY(1,1),
    [SiteID]                  INT NOT NULL,
    [LocTypeID]               INT NOT NULL,
    [X-Coord]                 FLOAT NOT NULL,
    [Y-Coord]                 FLOAT NOT NULL,
    [Species]                 NVARCHAR(255) NULL,
    [ChangeDate]              DATE NULL,
    [PlantingProjectYear]     INT NULL,
    [MetaData_ImportDateTime] DATETIME NOT NULL,
    [MetaData_ImportSource]   SMALLINT NOT NULL,
    CONSTRAINT [PK_Trees] PRIMARY KEY CLUSTERED (PK ASC),
    CONSTRAINT [FK_Trees_KeyValue_LocType] FOREIGN KEY ([LocTypeID]) REFERENCES [dbo].[KeyValue_LocType] ([ID]),
    CONSTRAINT [FK_Trees_KeyValue_ImportSource] FOREIGN KEY ([MetaData_ImportSource]) REFERENCES [dbo].[KeyValue_ImportSource] ([ID])
);


-- Create a table for rows in the staging table that contain validation errors. We can save
--      these for our review. Once the errors are fixed, then they can be inserted into the main Trees table.
CREATE TABLE [dbo].[TreeKeeper_Errors] (
    PK                        INT IDENTITY(1,1),
    [SiteID]                  INT NOT NULL,
    [LocTypeValue]            NVARCHAR(MAX) NULL,
    [X-Coord]                 FLOAT NULL,
    [Y-Coord]                 FLOAT NULL,
    [Species]                 NVARCHAR(MAX) NULL,
    [ChangeDate]              DATE NULL,
    [PlantingProjectValue]    NVARCHAR(MAX) NULL,
    [MetaData_ImportDateTime] DATETIME NOT NULL,
    [MetaData_ImportSource]   SMALLINT NOT NULL
    CONSTRAINT [PK_TreeKeeper_Errors] PRIMARY KEY CLUSTERED (PK ASC),
);



Next, we move all valid/clean rows from the staging table into the **Trees** table; any rows with invalid data are inserted into the TreeKeeper\_Errors table for later review.

In [ ]:
-- Insert the valid data into Trees
INSERT INTO Trees.dbo.Trees ( [SiteID], [LocTypeID], [X-Coord], [Y-Coord], [Species], [ChangeDate], [PlantingProjectYear], [MetaData_ImportDateTime], [MetaData_ImportSource] )
SELECT [Site ID],
    KeyValue_LocType.ID, 
    [X-Coord],
    [Y-Coord],
    [Species],
    [Change Date],
    CASE WHEN ISNUMERIC(SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4))=1 
      THEN SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4) 
      ELSE '0' END AS PlantingProjectYear,
    GETDATE(),
    '1' -- Source: Flat File
FROM TreeKeeper_Staging 
  INNER JOIN KeyValue_LocType
    ON KeyValue_LocType.Value = TreeKeeper_Staging.[Location Type for ISA value]
WHERE [Location Type for ISA value] IN ( 
    SELECT [KeyValue_LocType].Value
    FROM KeyValue_LocType )
  AND [X-Coord] IS NOT NULL
  AND [Y-Coord] IS NOT NULL
  AND LEN(Species)<=255

-- Insert the invalid data into TreeKeeper_Errors
INSERT INTO TreeKeeper_Errors
SELECT 
 [Site ID], 
 [Location Type for ISA value], 
 [X-Coord], 
 [Y-Coord], 
 Species, 
 [Change Date], 
 [Planting Project], 
 GETDATE(),
 '1' -- Source: Flat File
 from Treekeeper_Staging
 WHERE [Location Type for ISA value] NOT IN ( 
      SELECT [KeyValue_LocType].Value
      FROM KeyValue_LocType
  )
  OR [X-Coord] IS NULL
  OR [Y-Coord] IS NULL
  OR LEN(Species)>255

Next, work with your DBA to work through any errors in the table TreeKeeper\_Errors. Once the data integrity issues have been fixed, use the code below to add these columns to the Trees table.

If there were no errors found, skip this step.

In [ ]:
-- Once errored data has been cleaned up, use this code to move rows from Errors table to main Trees table
INSERT INTO Trees.dbo.Trees ( [SiteID], [LocTypeID], [X-Coord], [Y-Coord], [Species], [ChangeDate], [PlantingProjectYear], [MetaData_ImportDateTime], [MetaData_ImportSource] )
SELECT [SiteID],
    KeyValue_LocType.ID, 
    [X-Coord],
    [Y-Coord],
    [Species],
    [ChangeDate],
    CASE WHEN ISNUMERIC(SUBSTRING(TreeKeeper_Errors.[PlantingProjectValue],1,4))=1 
      THEN SUBSTRING(TreeKeeper_Errors.[PlantingProjectValue],1,4) 
      ELSE '0' END AS PlantingProjectYear,
    GETDATE(),
    '2' -- Source = Error Table
FROM TreeKeeper_Errors 
  INNER JOIN KeyValue_LocType
    ON KeyValue_LocType.Value = TreeKeeper_Errors.[LocTypeValue]
WHERE [LocTypeValue] IN ( 
    SELECT [KeyValue_LocType].Value
    FROM KeyValue_LocType )
  AND [X-Coord] IS NOT NULL
  AND [Y-Coord] IS NOT NULL
  AND LEN(Species)<=255

Finally, you can report on your data! Here are useful reports.

**Report #1 - Replica of "Final Data" sheet in Ella's Excel document**

In [ ]:
--Report #1: Produces a replica of "Final Data" sheet in Excel doc
USE Trees
GO
WITH tppView AS (
  SELECT [Site ID],
    [Location Type for ISA value], 
    SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4) AS PlantingProjectYear,
    [X-Coord],
    [Y-Coord],
    [Species],
    [Change Date]
  FROM TreeKeeper_Staging
  WHERE [Location Type for ISA value] = 'Street Tree (Boulevard)'
    OR [Location Type for ISA value] = 'Street Tree (Median)'
    OR [Location Type for ISA value] = 'Easement Tree'
    OR [Location Type for ISA value] = 'OtherCityProperty (Pol-Fir-PW-P&Scem-etc' ), 
tppCount AS (
  SELECT TreeKeeper_Staging.[Site ID] as 'Site ID',
    COUNT(DISTINCT SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4)) as 'Planting Project'
  FROM TreeKeeper_Staging
  GROUP BY TreeKeeper_Staging.[Site ID]
)

SELECT tppView.[Site ID],
  MAX(CASE WHEN ISNUMERIC(tppView.PlantingProjectYear) = 1 THEN 0 ELSE 1 END) AS [0000],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2011' THEN 1 ELSE 0 END) AS [2011],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2012' THEN 1 ELSE 0 END) AS [2012],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2013' THEN 1 ELSE 0 END) AS [2013],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2014' THEN 1 ELSE 0 END) AS [2014],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2015' THEN 1 ELSE 0 END) AS [2015],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2016' THEN 1 ELSE 0 END) AS [2016],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2017' THEN 1 ELSE 0 END) AS [2017],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2018' THEN 1 ELSE 0 END) AS [2018],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2019' THEN 1 ELSE 0 END) AS [2019],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2020' THEN 1 ELSE 0 END) AS [2020],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2021' THEN 1 ELSE 0 END) AS [2021],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2022' THEN 1 ELSE 0 END) AS [2022],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2023' THEN 1 ELSE 0 END) AS [2023],
  COUNT(DISTINCT tppView.PlantingProjectYear) AS [Grand Total]
FROM tppView
GROUP BY tppView.[Site ID],[X-Coord],[Y-Coord],[Location Type for ISA value]
ORDER BY [Site ID]

**Report #2 - Replica of "Final Data", but with additional columns**

In [ ]:
-- Report #2: Produces a replica of Ella's "Final Data" sheet, with additional useful columns like X-coord and Y-coord
WITH tppView AS (
  SELECT [Site ID],
    [Location Type for ISA value], 
    SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4) AS PlantingProjectYear,
    [X-Coord],
    [Y-Coord],
    [Species],
    [Change Date]
  FROM TreeKeeper_Staging
  WHERE [Location Type for ISA value] = 'Street Tree (Boulevard)'
    OR [Location Type for ISA value] = 'Street Tree (Median)'
    OR [Location Type for ISA value] = 'Easement Tree'
    OR [Location Type for ISA value] = 'OtherCityProperty (Pol-Fir-PW-P&Scem-etc' ), 
tppCount AS (
  SELECT TreeKeeper_Staging.[Site ID] as 'Site ID',
    COUNT(DISTINCT SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4)) as 'Planting Project'
  FROM TreeKeeper_Staging
  GROUP BY TreeKeeper_Staging.[Site ID]
)

SELECT tppView.[Site ID],
  MAX(CASE WHEN ISNUMERIC(tppView.PlantingProjectYear) = 1 THEN 0 ELSE 1 END) AS [0000],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2011' THEN 1 ELSE 0 END) AS [2011],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2012' THEN 1 ELSE 0 END) AS [2012],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2013' THEN 1 ELSE 0 END) AS [2013],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2014' THEN 1 ELSE 0 END) AS [2014],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2015' THEN 1 ELSE 0 END) AS [2015],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2016' THEN 1 ELSE 0 END) AS [2016],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2017' THEN 1 ELSE 0 END) AS [2017],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2018' THEN 1 ELSE 0 END) AS [2018],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2019' THEN 1 ELSE 0 END) AS [2019],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2020' THEN 1 ELSE 0 END) AS [2020],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2021' THEN 1 ELSE 0 END) AS [2021],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2022' THEN 1 ELSE 0 END) AS [2022],
  MAX(CASE WHEN tppView.PlantingProjectYear = '2023' THEN 1 ELSE 0 END) AS [2023],
  COUNT(DISTINCT tppView.PlantingProjectYear) AS [Grand Total],
  [Location Type for ISA value] AS LocType,
  [X-Coord],
  [Y-Coord],
  MIN([Change Date]) AS [EarliestChangeDate],
  MAX([Change Date]) AS [MostRecentChangeDate]
FROM tppView
GROUP BY tppView.[Site ID],[X-Coord],[Y-Coord],[Location Type for ISA value]

**Report #3:** ArcGIS import-able data for Site ID, Site Age, Site Mortality columns

In [2]:

--Report #3: GIS columns for Grand Total, Site Age, Site Mortality
USE Trees
GO
WITH tppView AS (
  SELECT [Site ID],
    [Location Type for ISA value], 
    CASE WHEN ISNUMERIC(SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4)) = 0 THEN NULL ELSE SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4) END AS PlantingProjectYear,
    [X-Coord],
    [Y-Coord],
    [Species],
    [Change Date]
  FROM TreeKeeper_Staging
  WHERE [Location Type for ISA value] = 'Street Tree (Boulevard)'
    OR [Location Type for ISA value] = 'Street Tree (Median)'
    OR [Location Type for ISA value] = 'Easement Tree'
    OR [Location Type for ISA value] = 'OtherCityProperty (Pol-Fir-PW-P&Scem-etc' ), 
tppCount AS (
  SELECT TreeKeeper_Staging.[Site ID] as 'Site ID',
    COUNT(DISTINCT SUBSTRING(TreeKeeper_Staging.[Planting Project],1,4)) as 'Planting Project'
  FROM TreeKeeper_Staging
  GROUP BY TreeKeeper_Staging.[Site ID]
)

SELECT tppView.[Site ID],
  COUNT(DISTINCT tppView.PlantingProjectYear) AS [Grand Total],
  YEAR(GETDATE()) - MIN(tppView.PlantingProjectYear) AS [Site Age],
  (1.0*COUNT(DISTINCT tppView.PlantingProjectYear) - 1) / (YEAR(GETDATE()) - MIN(tppView.PlantingProjectYear)) AS [Site Mortality],
  FORMAT((1.0*COUNT(DISTINCT tppView.PlantingProjectYear) - 1) / (YEAR(GETDATE()) - MIN(tppView.PlantingProjectYear)),'P0') AS [Site Mortality as %]
FROM tppView
GROUP BY tppView.[Site ID],[X-Coord],[Y-Coord],[Location Type for ISA value]
ORDER BY [Site ID]

Commands completed successfully.

Warning: Null value is eliminated by an aggregate or other SET operation.

(4362 rows affected)

Total execution time: 00:00:02.643

Site ID 0000 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020 2021 2022 2023 Grand Total Site Age Site Mortality Site Mortality as % 9367 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9370 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9371 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9373 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9374 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9400 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 9410 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9414 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9415 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9426 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9431 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9437 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9438 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 9439 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 10153 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 10160 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 10162 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 10168 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 44863 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 58946 0 0 0 0 1 0 0 0 0 0 0 1 0 0 2 9 0.111111111111 11% 61957 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61961 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61962 1 0 0 0 0 0 0 0 0 1 0 0 0 0 1 4 0.000000000000 0% 61963 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61964 0 0 0 0 1 0 0 0 1 1 0 0 0 0 3 9 0.222222222222 22% 61965 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61967 0 0 0 0 1 0 0 0 0 1 0 1 0 0 3 9 0.222222222222 22% 61968 0 0 0 0 1 1 1 1 0 0 1 0 0 0 5 9 0.444444444444 44% 61969 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61970 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61971 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61972 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 61973 1 0 0 0 0 0 0 1 0 0 0 0 0 0 1 6 0.000000000000 0% 61974 1 0 0 0 0 0 0 1 0 1 0 0 0 0 2 6 0.166666666666 17% 61975 1 0 0 0 0 0 1 1 0 1 0 0 0 0 3 7 0.285714285714 29% 61976 1 0 0 0 0 0 0 1 0 1 0 0 0 0 2 6 0.166666666666 17% 62101 0 0 0 1 0 1 1 0 0 0 0 0 0 0 3 10 0.200000000000 20% 62103 1 0 0 0 0 0 0 1 0 0 0 0 0 0 1 6 0.000000000000 0% 62105 1 0 0 0 0 1 1 0 0 0 0 0 0 0 2 8 0.125000000000 13% 62106 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62107 0 0 0 1 0 0 0 0 0 0 0 0 0 0 1 10 0.000000000000 0% 62108 1 0 0 0 0 1 0 0 0 0 0 0 0 0 1 8 0.000000000000 0% 62110 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62113 1 1 0 0 0 0 0 0 0 0 0 0 0 0 1 12 0.000000000000 0% 62114 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62115 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62116 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62117 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62118 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62119 1 0 0 0 0 0 0 1 0 0 0 0 0 0 1 6 0.000000000000 0% 62120 1 0 0 0 0 0 0 1 0 0 0 0 0 0 1 6 0.000000000000 0% 62121 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62122 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62127 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62128 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62129 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62130 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62131 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62132 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62133 1 0 0 0 0 0 1 0 0 1 0 1 0 0 3 7 0.285714285714 29% 62134 1 0 0 0 0 0 1 0 0 1 1 0 1 0 4 7 0.428571428571 43% 62135 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62136 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62137 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62139 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62140 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62141 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62142 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62144 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62147 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62148 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62149 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62150 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 NULL NULL NULL 62151 1 0 0 